![Microsoft](https://raw.githubusercontent.com/microsoft/azuredatastudio/main/extensions/resource-deployment/images/microsoft-small-logo.png)
## Run SQL Server 2022 Preview container image with Docker
This notebook will use Docker to pull and run the SQL Server 2022 Preview container image and connect to it in Azure Data Studio

### Dependencies
- Docker Engine. For more information, see [Install Docker](https://docs.docker.com/engine/installation/).

<span style="color:red"><font size="3">Please press the "Run all" button to run the notebook</font></span>

### Check dependencies

In [1]:
import sys,os,getpass,json,html,time
from string import Template

def run_command(displayCommand = ""):
    print("Executing: " + displayCommand if displayCommand != "" else cmd)
    !{cmd}
    if _exit_code != 0:
        sys.exit(f'Command execution failed with exit code: {str(_exit_code)}.\n')
    print(f'Command successfully executed')

cmd = 'docker version'
run_command()

: Msg 156, Level 15, State 1, Line 2
Incorrect syntax near the keyword 'from'.

: Msg 1038, Level 15, State 4, Line 4
An object or column name is missing or empty. For SELECT INTO statements, verify each column has a name. For other statements, look for empty alias names. Aliases defined as "" or [] are not allowed. Change the alias to a valid name.

: Msg 128, Level 15, State 1, Line 5
The name "Executing: " is not permitted in this context. Valid expressions are constants, constant expressions, and (in some contexts) variables. Column names are not permitted.

: Msg 1038, Level 15, State 4, Line 5
An object or column name is missing or empty. For SELECT INTO statements, verify each column has a name. For other statements, look for empty alias names. Aliases defined as "" or [] are not allowed. Change the alias to a valid name.

: Msg 156, Level 15, State 1, Line 5
Incorrect syntax near the keyword 'else'.

: Msg 102, Level 15, State 1, Line 7
Incorrect syntax near ':'.

: Msg 128, Level 15, State 1, Line 9
The name "f" is not permitted in this context. Valid expressions are constants, constant expressions, and (in some contexts) variables. Column names are not permitted.

Total execution time: 00:00:00.061

### List existing containers
You can view the ports that have been used by existing containers

In [ ]:
cmd = f'docker ps -a'
run_command()

### Required information

In [ ]:
env_var_flag = "AZDATA_NB_VAR_DOCKER_PASSWORD" in os.environ
password_name = 'SQL Server sa account password'
if env_var_flag:
    sql_password = os.environ["AZDATA_NB_VAR_DOCKER_PASSWORD"]
    sql_port = os.environ["AZDATA_NB_VAR_DOCKER_PORT"]
else:
    sql_password = getpass.getpass(prompt = password_name)
    password_confirm = getpass.getpass(prompt = f'Confirm {password_name}')
    if sql_password != password_confirm:
        raise SystemExit(f'{password_name} does not match the confirmation password.')
    sql_port = input('SQL Server port, default value is 1433')
    if len(sql_port) == 0:
        sql_port = '1433'
print(f'{password_name}: ******')
print(f'Port: {sql_port}')

### Pull the container image

In [ ]:
cmd = f'docker pull mcr.microsoft.com/mssql/server:2022-latest'
run_command()

### Start a new container

In [ ]:
if env_var_flag:
    container_name = os.environ["AZDATA_NB_VAR_DOCKER_CONTAINER_NAME"]
else:
    container_name = 'sql2022-' + time.strftime("%Y%m%d%H%M%S", time.localtime())
print('New container name: ' + container_name)

template = Template(f'docker run -e ACCEPT_EULA=Y -e "SA_PASSWORD=$password" -p {sql_port}:1433 --name {container_name} -d mcr.microsoft.com/mssql/server:2022-latest')
cmd = template.substitute(password=sql_password)
run_command(template.substitute(password='******'))

### List all the containers

In [ ]:
cmd = f'docker ps -a'
run_command()

### Connect to SQL Server in Azure Data Studio
It might take a couple minutes for SQL Server to launch

In [ ]:
from IPython.display import *
connectionParameter = '{"serverName":"localhost,' + sql_port + '","providerName":"MSSQL","authenticationType":"SqlLogin","userName":"sa","password":' + json.dumps(sql_password) + '}'
display(HTML('<br/><a href="command:azdata.connect?' + html.escape(connectionParameter)+'"><font size="3">Click here to connect to SQL Server</font></a><br/>'))
display(HTML('<br/><span style="color:red"><font size="2">NOTE: The SQL Server password is included in this link, you may want to clear the results of this code cell before saving the notebook.</font></span>'))

### Stop and remove the container

In [ ]:
stop_container_command = f'docker stop {container_name}'
remove_container_command = f'docker rm {container_name}'
display(HTML("Use this link to: <a href=\"command:workbench.action.terminal.focus\">open the terminal window in Azure Data Studio</a> and use the links below to paste the command to the terminal."))
display(HTML("Stop the container: <a href=\"command:workbench.action.terminal.sendSequence?%7B%22text%22%3A%22"+stop_container_command.replace(" ","%20")+"%22%7D\">" + stop_container_command + "</a>"))
display(HTML("Remove the container: <a href=\"command:workbench.action.terminal.sendSequence?%7B%22text%22%3A%22"+remove_container_command.replace(" ","%20")+"%22%7D\">" + remove_container_command + "</a>"))

Create New database name "TutorialDB"

In [1]:
USE master
GO
IF NOT EXISTS (
 SELECT name
 FROM sys.databases
 WHERE name = N'TutorialDB'
)
 CREATE DATABASE [TutorialDB];

GO
ALTER DATABASE [TutorialDB] SET QUERY_STORE = ON;

USE [master]

ALTER DATABASE TutorialDB
SET MULTI_USER
WITH ROLLBACK IMMEDIATE


Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.424

In [3]:
USE master
GO
IF NOT EXISTS (
 SELECT name
 FROM sys.databases
 WHERE name = N'USERS_DB'
)
 CREATE DATABASE [USERS_DB];

GO
ALTER DATABASE [USERS_DB] SET QUERY_STORE = ON;

USE [master]

ALTER DATABASE USERS_DB
SET MULTI_USER
WITH ROLLBACK IMMEDIATE

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:01.108

In [14]:
GO
DROP DATABASE TutorialDB

: Msg 3702, Level 16, State 4, Line 2
Cannot drop database "TutorialDB" because it is currently in use.

Total execution time: 00:00:20.254

Make table in database

In [6]:
USE TutorialDB
GO
--Khởi tạo Table LASER P3
CREATE TABLE LASER_P3_PFA
(
            ITEM NVARCHAR(1000),
            CATALOG_NAME NVARCHAR(1000),
            PARA_NAME NVARCHAR(1000),
            POR_VALUE NVARCHAR(1000),
            PRIORITY_VALUE NVARCHAR(1000),
            TOOL_VALUE NVARCHAR(1000),
            CE NVARCHAR(1000)
)
GO
CREATE TABLE LASER_P3_PFB
(
            ITEM NVARCHAR(1000),
            CATALOG_NAME NVARCHAR(1000),
            PARA_NAME NVARCHAR(1000),
            POR_VALUE NVARCHAR(1000),
            PRIORITY_VALUE NVARCHAR(1000),
            TOOL_VALUE NVARCHAR(1000),
            CE NVARCHAR(1000)
)
GO
CREATE TABLE LASER_P3_PFC
(
            ITEM NVARCHAR(1000),
            CATALOG_NAME NVARCHAR(1000),
            PARA_NAME NVARCHAR(1000),
            POR_VALUE NVARCHAR(1000),
            PRIORITY_VALUE NVARCHAR(1000),
            TOOL_VALUE NVARCHAR(1000),
            CE NVARCHAR(1000)
)
GO


Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.094

In [6]:
USE USERS_DB
GO
CREATE TABLE USERS
(
    ID INT,
    USER_NAME NVARCHAR(1000),
    EMAIL NVARCHAR(1000),
    PASS_WORD NVARCHAR(1000),
    PRIMARY KEY CLUSTERED (ID ASC)
)
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.100

In [5]:
USE USERS_DB
GO 
DROP TABLE USERS;

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.125

In [ ]:
USE USERS_DB
GO
Select * from USERS

In [5]:
USE TutorialDB
GO
--Xoá table
DROP TABLE LASER_P3_PFA, LASER_P3_PFB, LASER_P3_PFC;

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.062

In [ ]:
USE TutorialDB
GO
--Xoá table
DELETE FROM LASER_P3_PF;

In [2]:
USE TutorialDB
GO

Select * from LASER_P3_PFA
Select * from LASER_P3_PFB
Select * from LASER_P3_PFC

Commands completed successfully.

(7770 rows affected)

(7400 rows affected)

(7400 rows affected)

Displaying Top 5000 rows.

...

Displaying Top 5000 rows.

Total execution time: 00:00:01.182

ITEM CATALOG_NAME PARA_NAME POR_VALUE PRIORITY_VALUE TOOL_VALUE CE MC2 Recipe on/off None R 1 NULL MC3 Recipe Relative positioning None R 0 NULL MC4 Recipe step None R 0 NULL MC5 Recipe One Y positioning, if failed None R 0 NULL MC6 Recipe Stop after cycle if failed None R 0 NULL MC7 Recipe No scribing if failed None R 0 NULL MC8 Recipe Interaction every substrate None R 0 NULL MC9 Recipe Interaction if failed None R 1 NULL MC10 Recipe after # substrates None R 1 NULL MC11 Recipe Calculation of beam pitch correction factor None R 1 NULL MC12 Recipe Calculation extension factor Y None A 1 NULL MC13 Recipe Cameras to Use None None None NULL MC14 Recipe Camera 1 None R 1 NULL MC15 Recipe Selection line None R 0 NULL MC16 Recipe Camera 2 None R 1 NULL MC17 Recipe Selection line None R 0 NULL MC18 Recipe Camera 3 (for P2/P3) None A 1 NULL MC19 Recipe Selection line None A 0 NULL MC20 Recipe Dead zone inspection parameter None None None NULL MC21 Recipe on/off On R 1 NULL MC22 Recipe Section 1 None None None NULL MC23 Recipe Number of lines 135 R 135 NULL MC24 Recipe Lower limit 0.077 R 0.077 NULL MC25 Recipe Nominal value 0.1 R 0.1 NULL MC26 Recipe Upper limit 0.132 R 0.132 NULL MC27 Recipe Lower limit Std dev -1 R None NULL MC28 Recipe Upper limit Std dev -1 R None NULL MC29 Recipe Section 2 None None None NULL MC30 Recipe Number of lines 132 R 132 NULL MC31 Recipe Lower limit 0.077 R 0.077 NULL MC32 Recipe Nominal value 0.1 R 0.1 NULL MC33 Recipe Upper limit 0.132 R 0.132 NULL MC34 Recipe Lower limit Std dev -1 R None NULL MC35 Recipe Upper limit Std dev -1 R None NULL MC36 Recipe Section 3 None None None NULL MC37 Recipe Number of lines 1 R 1 NULL MC38 Recipe Lower limit 0.077 R 0.05 NULL MC39 Recipe Nominal value 0.1 R 0.07 NULL MC40 Recipe Upper limit 0.132 R 0.1 NULL MC41 Recipe Lower limit Std dev -1 R None NULL MC42 Recipe Upper limit Std dev -1 R None NULL MC43 Recipe Path tracking (P2/P3 only) On R 1 NULL MC44 Beam group 1 Powermap None None None NULL MC45 Beam group 1 initial attenuation(%) 4 A 4 NULL MC46 Beam group 1 FiN/Al attenuation(%) 99 A 99 NULL MC47 Beam group 1 Attenuation increment(%) 5 A 10 NULL MC48 Beam group 1 Initial frequency(kHz) 1000 R 1000 NULL MC49 Beam group 1 FiN/Al frequency(kHz) 1000 R 1000 NULL MC50 Beam group 1 Frequency increment(kHz) 10 A 10 NULL MC51 Beam group 1 Laser measurement None None None NULL MC52 Beam group 1 Power window % 23 A 20 NULL MC53 Beam group 1 Error setting target power: check R 1 NULL MC54 Beam group 1 Faulty power measurement: check R 1 NULL MC55 Beam group 1 after _____ substrate power measurement 175 A 300 NULL MC56 Beam group 2 Powermap None None None NULL MC57 Beam group 2 initial attenuation(%) 4 A 4 NULL MC58 Beam group 2 FiN/Al attenuation(%) 99 A 99 NULL MC59 Beam group 2 Attenuation increment(%) 5 A 10 NULL MC60 Beam group 2 Initial frequency(kHz) 1000 R 1000 NULL MC61 Beam group 2 FiN/Al frequency(kHz) 1000 R 1000 NULL MC62 Beam group 2 Frequency increment(kHz) 10 A 10 NULL MC63 Beam group 2 Laser measurement None None None NULL MC64 Beam group 2 Power window % 23 A 20 NULL MC65 Beam group 2 Error setting target power: check R 1 NULL MC66 Beam group 2 Faulty power measurement: check R 1 NULL MC67 Beam group 2 after _____ substrate power measurement 175 A 300 NULL MC68 Handling 3 Each temperature in log file Uncheck R 0 NULL MC69 Handling 3 Temperature measurement as warning in log file Uncheck R 0 NULL MC70 Handling 3 DryCycle Uncheck R None NULL MC71 Handling 3 Reverse Loading Uncheck R None NULL MC72 Handling 3 Alarm substrate outfeed not possible 10000.0 Sec R 10000 NULL MC73 General Delete old files after(days) 30 R 30 NULL MC74 General Repeat mainteN/Ance message after(sec) 86400 R 86400 NULL MC75 General OPC communication switched on Check R 1 NULL MC76 General Log time per step Uncheck R None NULL MC77 Beam Group 1 subheading Beam 1 to Beam 12/On/Off/Debug information Check R None NULL MC78 Beam Group 1 subheading upper limit of interN/Al laser power(W)

ITEM CATALOG_NAME PARA_NAME POR_VALUE PRIORITY_VALUE TOOL_VALUE CE MC161 Camera 1 Y: 58.085 R 57.265 NULL MC162 Camera 1 X reference (mm): 1700 R 300 NULL MC163 Camera 1 Y: 58.085 R 57.407 NULL MC164 Camera 1 Camera 3 None None None NULL MC165 Camera 1 Installed Check R 1 NULL MC166 Camera 1 Type: horizontal structure R 2 NULL MC167 Camera 1 Selection of line 1 of 2 R 1 NULL MC168 Camera 1 X position (mm): 1700 R 1700 NULL MC169 Camera 1 Y: 58.085 R 1203.385 NULL MC170 Camera 1 X reference (mm): 1700 R 1700 NULL MC171 Camera 1 Y: 58.085 R 1202.085 NULL MC172 Camera 1 Camera 4 None None None NULL MC173 Camera 1 Installed Check R None NULL MC174 Camera 1 Type: horizontal structure R None NULL MC175 Camera 1 Selection of line 1 of 2 R None NULL MC176 Camera 1 X position (mm): 1700 R None NULL MC177 Camera 1 Y: 58.085 R None NULL MC178 Camera 1 X reference (mm): 1700 R None NULL MC179 Camera 1 Y: 58.085 R None NULL MC180 Camera 1 Camera 5 None None None NULL MC181 Camera 1 Installed Check R 1 NULL MC182 Camera 1 Type: Path tracking R 6 NULL MC183 Camera 1 Selection of line 1 of 1 R 1 NULL MC184 Camera 1 X reference (mm): 0 R 0 NULL MC185 Camera 1 Y: 0 R 0 NULL MC186 Camera 1 Camera 6 None None None NULL MC187 Camera 1 Installed Check R 1 NULL MC188 Camera 1 Type: Path tracking R 6 NULL MC189 Camera 1 Selection of line 1 of 1 R 1 NULL MC190 Camera 1 X reference (mm): 0 R 0 NULL MC191 Camera 1 Y: 0 R 0 NULL MC192 Camera 1 Camera 9 None None None NULL MC193 Camera 1 Installed Check R None NULL MC194 Camera 1 Type: horizontal structure R None NULL MC195 Camera 1 Selection of line 1 of 2 R None NULL MC196 Camera 1 X reference (mm): 1700 R None NULL MC197 Camera 1 Y: 58.085 R None NULL MC198 Camera 1 Auto inspection: Check R 1 NULL MC199 Camera 1 Image File name: Default R C:\First Solar Data Files\Inspec\ NULL MC200 Camera 1 Transmitted light: Check R 1 NULL MC201 Camera 2 Y lines angle calculation from angle of X lines (rectangular structure): Check R 1 NULL MC202 Camera 2 Save image if referencing failed; Check R 1 NULL MC203 Camera 2 Image path: c:\Reference Failed R C:\Reference failed NULL MC204 Camera 2 Waiting time for take image while referencing 0 sec R 0 NULL MC205 Camera 2 waiting time for end of movement with simulsted camera 5.0 sec R 5 NULL MC206 Camera 2 Dead zone inspection parameter None R None NULL MC207 Camera 2 Available Check R 1 NULL MC208 Camera 2 on/off Check R 1 NULL MC209 Camera 2 stop in case of error Check R 0 NULL MC210 Camera 2 signal tone and warning Uncheck R 0 NULL MC211 Camera 2 warning Uncheck R 0 NULL MC212 Camera 2 allowed errors per substrate 30 on 4 subtrates in the Row R 30 NULL MC213 Camera 2 save result at C:\First Solar Data Files\DeadZone R C:\First Solar Data Files\DeadZone NULL MC214 Camera 2 camera name '1st camera' C1mera R C1mera NULL MC215 Camera 2 camera name '2nd camera' C2mera R C2mera NULL MC216 Camera 2 camera name '3rd camera' C3mera R C3mera NULL MC217 Camera 2 camera name '4th camera' C4mera R C4mera NULL MC218 Camera 2 camera name '5th camera' C5mera R C5mera NULL MC219 Camera 2 Maximum offset in warm-up phase (mm) 0 R 0 NULL MC220 Autofocus tracking Error No Value __ Stop Of Arrangement check R 1 NULL MC221 Autofocus tracking Save results at C:\First Solar Data Files\Focal R C:\First Solar Data Files\Focal NULL MC222 Beam Diagnostic Target Power 2.5 A None NULL MC223 Beam Diagnostic Drive to power meas. Position check/uncheck check A None NULL MC224 Beam Diagnostic Drive X axis continuously uncheck A None NULL MC225 Beam Diagnostic sec. waiting time 1 A None NULL MC226 Beam Diagnostic Utilization line uncheck A None NULL MC227 Beam Diagnostic Position X mm 500 A None NULL MC228 Beam Diagnostic Position Y mm 200 A None NULL MC229 Beam Diagnostic Pulse Length sec. 0.1 A None NULL MC230 Beam Diagnostic Target power 2.5 A None NULL MC231 Beam Diagnostic every substrate (min) -1 A None NULL MC232 Beam Diagnostic every substrate (max) -1 A None NULL MC233 Beam Diagnostic after more 

ITEM CATALOG_NAME PARA_NAME POR_VALUE PRIORITY_VALUE TOOL_VALUE CE MC2 Recipe on/off None R 1 NULL MC3 Recipe Relative positioning None R 0 NULL MC4 Recipe step None R 0 NULL MC5 Recipe One Y positioning, if failed None R 0 NULL MC6 Recipe Stop after cycle if failed None R 0 NULL MC7 Recipe No scribing if failed None R 0 NULL MC8 Recipe Interaction every substrate None R 0 NULL MC9 Recipe Interaction if failed None R 1 NULL MC10 Recipe after # substrates None R 1 NULL MC11 Recipe Calculation of beam pitch correction factor None R 1 NULL MC12 Recipe Calculation extension factor Y None A 1 NULL MC13 Recipe Cameras to Use None None None NULL MC14 Recipe Camera 1 None R 1 NULL MC15 Recipe Selection line None R 0 NULL MC16 Recipe Camera 2 None R 1 NULL MC17 Recipe Selection line None R 0 NULL MC18 Recipe Camera 3 (for P2/P3) None A 1 NULL MC19 Recipe Selection line None A 0 NULL MC20 Recipe Dead zone inspection parameter None None None NULL MC21 Recipe on/off On R 1 NULL MC22 Recipe Section 1 None None None NULL MC23 Recipe Number of lines 135 R 135 NULL MC24 Recipe Lower limit 0.077 R 0.077 NULL MC25 Recipe Nominal value 0.1 R 0.1 NULL MC26 Recipe Upper limit 0.132 R 0.132 NULL MC27 Recipe Lower limit Std dev -1 R None NULL MC28 Recipe Upper limit Std dev -1 R None NULL MC29 Recipe Section 2 None None None NULL MC30 Recipe Number of lines 132 R 132 NULL MC31 Recipe Lower limit 0.077 R 0.077 NULL MC32 Recipe Nominal value 0.1 R 0.1 NULL MC33 Recipe Upper limit 0.132 R 0.132 NULL MC34 Recipe Lower limit Std dev -1 R None NULL MC35 Recipe Upper limit Std dev -1 R None NULL MC36 Recipe Section 3 None None None NULL MC37 Recipe Number of lines 1 R 1 NULL MC38 Recipe Lower limit 0.077 R 0.05 NULL MC39 Recipe Nominal value 0.1 R 0.07 NULL MC40 Recipe Upper limit 0.132 R 0.1 NULL MC41 Recipe Lower limit Std dev -1 R None NULL MC42 Recipe Upper limit Std dev -1 R None NULL MC43 Recipe Path tracking (P2/P3 only) On R 1 NULL MC44 Beam group 1 Powermap None None None NULL MC45 Beam group 1 initial attenuation(%) 4 A 4 NULL MC46 Beam group 1 FiN/Al attenuation(%) 99 A 99 NULL MC47 Beam group 1 Attenuation increment(%) 5 A 10 NULL MC48 Beam group 1 Initial frequency(kHz) 1000 R 1000 NULL MC49 Beam group 1 FiN/Al frequency(kHz) 1000 R 1000 NULL MC50 Beam group 1 Frequency increment(kHz) 10 A 10 NULL MC51 Beam group 1 Laser measurement None None None NULL MC52 Beam group 1 Power window % 23 A 20 NULL MC53 Beam group 1 Error setting target power: check R 1 NULL MC54 Beam group 1 Faulty power measurement: check R 1 NULL MC55 Beam group 1 after _____ substrate power measurement 175 A 300 NULL MC56 Beam group 2 Powermap None None None NULL MC57 Beam group 2 initial attenuation(%) 4 A 4 NULL MC58 Beam group 2 FiN/Al attenuation(%) 99 A 99 NULL MC59 Beam group 2 Attenuation increment(%) 5 A 10 NULL MC60 Beam group 2 Initial frequency(kHz) 1000 R 1000 NULL MC61 Beam group 2 FiN/Al frequency(kHz) 1000 R 1000 NULL MC62 Beam group 2 Frequency increment(kHz) 10 A 10 NULL MC63 Beam group 2 Laser measurement None None None NULL MC64 Beam group 2 Power window % 23 A 20 NULL MC65 Beam group 2 Error setting target power: check R 1 NULL MC66 Beam group 2 Faulty power measurement: check R 1 NULL MC67 Beam group 2 after _____ substrate power measurement 175 A 300 NULL MC68 Handling 3 Each temperature in log file Uncheck R 0 NULL MC69 Handling 3 Temperature measurement as warning in log file Uncheck R 0 NULL MC70 Handling 3 DryCycle Uncheck R None NULL MC71 Handling 3 Reverse Loading Uncheck R None NULL MC72 Handling 3 Alarm substrate outfeed not possible 10000.0 Sec R 10000 NULL MC73 General Delete old files after(days) 30 R 30 NULL MC74 General Repeat mainteN/Ance message after(sec) 86400 R 86400 NULL MC75 General OPC communication switched on Check R 1 NULL MC76 General Log time per step Uncheck R None NULL MC77 Beam Group 1 subheading Beam 1 to Beam 12/On/Off/Debug information Check R None NULL MC78 Beam Group 1 subheading upper limit of interN/Al laser power(W)

In [3]:
USE master
GO
IF NOT EXISTS (
 SELECT name
 FROM sys.databases
 WHERE name = N'CE_Control_Plan'
)
 CREATE DATABASE [CE_Control_Plan];

GO
ALTER DATABASE [CE_Control_Plan] SET QUERY_STORE = ON;

USE [master]

ALTER DATABASE CE_Control_Plan
SET MULTI_USER
WITH ROLLBACK IMMEDIATE


Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.977

Table Control\_plan Laser

In [45]:
USE CE_Control_Plan

GO
DROP TABLE LASER_P3_CONTROL_PLAN

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.353

In [7]:
USE CE_Control_Plan

CREATE TABLE LASER_P3_CONTROL_PLAN_A
(
            ITEM NVARCHAR(1000),
            CATALOG_NAME NVARCHAR(1000),
            PARA_NAME NVARCHAR(1000),
            POR_VALUE NVARCHAR(1000),
            PRIORITY_VALUE NVARCHAR(1000),
            TAG_NAME NVARCHAR(1000),
            GU_ID NVARCHAR(1000)
)
GO

CREATE TABLE LASER_P3_CONTROL_PLAN_B
(
            ITEM NVARCHAR(1000),
            CATALOG_NAME NVARCHAR(1000),
            PARA_NAME NVARCHAR(1000),
            POR_VALUE NVARCHAR(1000),
            PRIORITY_VALUE NVARCHAR(1000),
            TAG_NAME NVARCHAR(1000),
            GU_ID NVARCHAR(1000)
)
GO
CREATE TABLE LASER_P3_CONTROL_PLAN_C
(
            ITEM NVARCHAR(1000),
            CATALOG_NAME NVARCHAR(1000),
            PARA_NAME NVARCHAR(1000),
            POR_VALUE NVARCHAR(1000),
            PRIORITY_VALUE NVARCHAR(1000),
            TAG_NAME NVARCHAR(1000),
            GU_ID NVARCHAR(1000)
)
GO


Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.183

In [49]:
USE CE_Control_Plan
GO

DELETE FROM LASER_P3_CONTROL_PLAN

Commands completed successfully.

(370 rows affected)

Total execution time: 00:00:00.337

In [1]:
USE CE_Control_Plan
GO

Select * from LASER_P3_CONTROL_PLAN_A;
Select * from LASER_P3_CONTROL_PLAN_B;
Select * from LASER_P3_CONTROL_PLAN_C;

Commands completed successfully.

(370 rows affected)

(370 rows affected)

(370 rows affected)

Total execution time: 00:00:00.321

ITEM CATALOG_NAME PARA_NAME POR_VALUE PRIORITY_VALUE TAG_NAME GU_ID MC2 Recipe on/off None R Referenzierung aktiv None MC3 Recipe Relative positioning None R relative Position für Referenzierung None MC4 Recipe step None R Referenzierung mit Positionierung None MC5 Recipe One Y positioning, if failed None R eine Y Positionierung, wenn fehlgeschlagen None MC6 Recipe Stop after cycle if failed None R Halt nach Taktende, wenn keine Referenzierung None MC7 Recipe No scribing if failed None R keine Strukturierung, wenn keine Referenzierung None MC8 Recipe Interaction every substrate None R immer Interaktion None MC9 Recipe Interaction if failed None R Interaktion, wenn keine Referenzierung None MC10 Recipe after # substrates None R Interaktion nach Anzahl der Substrate None MC11 Recipe Calculation of beam pitch correction factor None R Kalkulation Strahlabstandskorrekturfaktor None MC12 Recipe Calculation extension factor Y None A Kalkulation Dehnungsfaktor Y None MC13 Recipe Cameras to Use None None None None MC14 Recipe Camera 1 None R Kamera 1 verwenden None MC15 Recipe Selection line None R Auswahl Linie - Kamera 1 None MC16 Recipe Camera 2 None R Kamera 2 verwenden None MC17 Recipe Selection line None R Auswahl Linie - Kamera 2 None MC18 Recipe Camera 3 (for P2/P3) None A Kamera 3 verwenden None MC19 Recipe Selection line None A Auswahl Linie - Kamera 3 None MC20 Recipe Dead zone inspection parameter None None None None MC21 Recipe on/off On R ISIS eingeschaltet None MC22 Recipe Section 1 None None None None MC23 Recipe Number of lines 135 R 1. Bereich Anzahl Linien None MC24 Recipe Lower limit 0.077 R 1. Bereich untere Grenze None MC25 Recipe Nominal value 0.1 R 1. Bereich Sollwert None MC26 Recipe Upper limit 0.132 R 1. Bereich obere Grenze None MC27 Recipe Lower limit Std dev -1 R None None MC28 Recipe Upper limit Std dev -1 R None None MC29 Recipe Section 2 None None None None MC30 Recipe Number of lines 132 R 2. Bereich Anzahl Linien None MC31 Recipe Lower limit 0.077 R 2. Bereich untere Grenze None MC32 Recipe Nominal value 0.1 R 2. Bereich Sollwert None MC33 Recipe Upper limit 0.132 R 2. Bereich obere Grenze None MC34 Recipe Lower limit Std dev -1 R None None MC35 Recipe Upper limit Std dev -1 R None None MC36 Recipe Section 3 None None None None MC37 Recipe Number of lines 1 R 3. Bereich Anzahl Linien None MC38 Recipe Lower limit 0.077 R 3. Bereich untere Grenze None MC39 Recipe Nominal value 0.1 R 3. Bereich Sollwert None MC40 Recipe Upper limit 0.132 R 3. Bereich obere Grenze None MC41 Recipe Lower limit Std dev -1 R None None MC42 Recipe Upper limit Std dev -1 R None None MC43 Recipe Path tracking (P2/P3 only) On R Bahnverfolgung Rezept eingeschaltet None MC44 Beam group 1 Powermap None None None None MC45 Beam group 1 initial attenuation(%) 4 A Attenuation low (%) 342bb397-526a-4949-bc31-d992bc8fbe80 MC46 Beam group 1 FiN/Al attenuation(%) 99 A Attenuation high (%) 1248b408-8ebe-4a92-8f1c-b2a6593a3297 MC47 Beam group 1 Attenuation increment(%) 5 A Attenuation step (%) 27486c1d-8c5b-47fe-91b1-abffbbcec9a4 MC48 Beam group 1 Initial frequency(kHz) 1000 R Frequenz low [kHz] 78c62ff7-0d8f-45b0-b061-bdc3b97271a2 MC49 Beam group 1 FiN/Al frequency(kHz) 1000 R Frequenz high [kHz] ec972836-f12b-4740-a3d7-162989cc43b2 MC50 Beam group 1 Frequency increment(kHz) 10 A Frequenz step [kHz] 94ffba7f-60b3-4d9a-bf4e-7bb8fdc63907 MC51 Beam group 1 Laser measurement None None None None MC52 Beam group 1 Power window % 23 A erlaubte Abweichung externe Leistung [%] d1b66ce6-6898-4c77-9682-8b1bf1516949 MC53 Beam group 1 Error setting target power: check R Anlagenstopp bei Fehler Setzen der Sollleistung 49ab3617-989c-436a-be41-7ee1ae60446a MC54 Beam group 1 Faulty power measurement: check R Anlagenstop bei Leistungsmessfehler c7aa2ada-d1de-4d84-b840-44cb47ea1841 MC55 Beam group 1 after _____ substrate power measurement 175 A Zyklus Leistungsmessung b00f6248-a0c1-4389-8b40-550eca311968 MC56 Beam group 2 Powermap None None None None MC57 Be

ITEM CATALOG_NAME PARA_NAME POR_VALUE PRIORITY_VALUE TAG_NAME GU_ID MC2 Recipe on/off None R Referenzierung aktiv None MC3 Recipe Relative positioning None R relative Position für Referenzierung None MC4 Recipe step None R Referenzierung mit Positionierung None MC5 Recipe One Y positioning, if failed None R eine Y Positionierung, wenn fehlgeschlagen None MC6 Recipe Stop after cycle if failed None R Halt nach Taktende, wenn keine Referenzierung None MC7 Recipe No scribing if failed None R keine Strukturierung, wenn keine Referenzierung None MC8 Recipe Interaction every substrate None R immer Interaktion None MC9 Recipe Interaction if failed None R Interaktion, wenn keine Referenzierung None MC10 Recipe after # substrates None R Interaktion nach Anzahl der Substrate None MC11 Recipe Calculation of beam pitch correction factor None R Kalkulation Strahlabstandskorrekturfaktor None MC12 Recipe Calculation extension factor Y None A Kalkulation Dehnungsfaktor Y None MC13 Recipe Cameras to Use None None None None MC14 Recipe Camera 1 None R Kamera 1 verwenden None MC15 Recipe Selection line None R Auswahl Linie - Kamera 1 None MC16 Recipe Camera 2 None R Kamera 2 verwenden None MC17 Recipe Selection line None R Auswahl Linie - Kamera 2 None MC18 Recipe Camera 3 (for P2/P3) None A Kamera 3 verwenden None MC19 Recipe Selection line None A Auswahl Linie - Kamera 3 None MC20 Recipe Dead zone inspection parameter None None None None MC21 Recipe on/off On R ISIS eingeschaltet None MC22 Recipe Section 1 None None None None MC23 Recipe Number of lines 135 R 1. Bereich Anzahl Linien None MC24 Recipe Lower limit 0.077 R 1. Bereich untere Grenze None MC25 Recipe Nominal value 0.1 R 1. Bereich Sollwert None MC26 Recipe Upper limit 0.132 R 1. Bereich obere Grenze None MC27 Recipe Lower limit Std dev -1 R None None MC28 Recipe Upper limit Std dev -1 R None None MC29 Recipe Section 2 None None None None MC30 Recipe Number of lines 132 R 2. Bereich Anzahl Linien None MC31 Recipe Lower limit 0.077 R 2. Bereich untere Grenze None MC32 Recipe Nominal value 0.1 R 2. Bereich Sollwert None MC33 Recipe Upper limit 0.132 R 2. Bereich obere Grenze None MC34 Recipe Lower limit Std dev -1 R None None MC35 Recipe Upper limit Std dev -1 R None None MC36 Recipe Section 3 None None None None MC37 Recipe Number of lines 1 R 3. Bereich Anzahl Linien None MC38 Recipe Lower limit 0.077 R 3. Bereich untere Grenze None MC39 Recipe Nominal value 0.1 R 3. Bereich Sollwert None MC40 Recipe Upper limit 0.132 R 3. Bereich obere Grenze None MC41 Recipe Lower limit Std dev -1 R None None MC42 Recipe Upper limit Std dev -1 R None None MC43 Recipe Path tracking (P2/P3 only) On R Bahnverfolgung Rezept eingeschaltet None MC44 Beam group 1 Powermap None None None None MC45 Beam group 1 initial attenuation(%) 4 A Attenuation low (%) 342bb397-526a-4949-bc31-d992bc8fbe80 MC46 Beam group 1 FiN/Al attenuation(%) 99 A Attenuation high (%) 1248b408-8ebe-4a92-8f1c-b2a6593a3297 MC47 Beam group 1 Attenuation increment(%) 5 A Attenuation step (%) 27486c1d-8c5b-47fe-91b1-abffbbcec9a4 MC48 Beam group 1 Initial frequency(kHz) 1000 R Frequenz low [kHz] 78c62ff7-0d8f-45b0-b061-bdc3b97271a2 MC49 Beam group 1 FiN/Al frequency(kHz) 1000 R Frequenz high [kHz] ec972836-f12b-4740-a3d7-162989cc43b2 MC50 Beam group 1 Frequency increment(kHz) 10 A Frequenz step [kHz] 94ffba7f-60b3-4d9a-bf4e-7bb8fdc63907 MC51 Beam group 1 Laser measurement None None None None MC52 Beam group 1 Power window % 23 A erlaubte Abweichung externe Leistung [%] d1b66ce6-6898-4c77-9682-8b1bf1516949 MC53 Beam group 1 Error setting target power: check R Anlagenstopp bei Fehler Setzen der Sollleistung 49ab3617-989c-436a-be41-7ee1ae60446a MC54 Beam group 1 Faulty power measurement: check R Anlagenstop bei Leistungsmessfehler c7aa2ada-d1de-4d84-b840-44cb47ea1841 MC55 Beam group 1 after _____ substrate power measurement 175 A Zyklus Leistungsmessung b00f6248-a0c1-4389-8b40-550eca311968 MC56 Beam group 2 Powermap None None None None MC57 Be

ITEM CATALOG_NAME PARA_NAME POR_VALUE PRIORITY_VALUE TAG_NAME GU_ID MC2 Recipe on/off None R Referenzierung aktiv None MC3 Recipe Relative positioning None R relative Position für Referenzierung None MC4 Recipe step None R Referenzierung mit Positionierung None MC5 Recipe One Y positioning, if failed None R eine Y Positionierung, wenn fehlgeschlagen None MC6 Recipe Stop after cycle if failed None R Halt nach Taktende, wenn keine Referenzierung None MC7 Recipe No scribing if failed None R keine Strukturierung, wenn keine Referenzierung None MC8 Recipe Interaction every substrate None R immer Interaktion None MC9 Recipe Interaction if failed None R Interaktion, wenn keine Referenzierung None MC10 Recipe after # substrates None R Interaktion nach Anzahl der Substrate None MC11 Recipe Calculation of beam pitch correction factor None R Kalkulation Strahlabstandskorrekturfaktor None MC12 Recipe Calculation extension factor Y None A Kalkulation Dehnungsfaktor Y None MC13 Recipe Cameras to Use None None None None MC14 Recipe Camera 1 None R Kamera 1 verwenden None MC15 Recipe Selection line None R Auswahl Linie - Kamera 1 None MC16 Recipe Camera 2 None R Kamera 2 verwenden None MC17 Recipe Selection line None R Auswahl Linie - Kamera 2 None MC18 Recipe Camera 3 (for P2/P3) None A Kamera 3 verwenden None MC19 Recipe Selection line None A Auswahl Linie - Kamera 3 None MC20 Recipe Dead zone inspection parameter None None None None MC21 Recipe on/off On R ISIS eingeschaltet None MC22 Recipe Section 1 None None None None MC23 Recipe Number of lines 135 R 1. Bereich Anzahl Linien None MC24 Recipe Lower limit 0.077 R 1. Bereich untere Grenze None MC25 Recipe Nominal value 0.1 R 1. Bereich Sollwert None MC26 Recipe Upper limit 0.132 R 1. Bereich obere Grenze None MC27 Recipe Lower limit Std dev -1 R None None MC28 Recipe Upper limit Std dev -1 R None None MC29 Recipe Section 2 None None None None MC30 Recipe Number of lines 132 R 2. Bereich Anzahl Linien None MC31 Recipe Lower limit 0.077 R 2. Bereich untere Grenze None MC32 Recipe Nominal value 0.1 R 2. Bereich Sollwert None MC33 Recipe Upper limit 0.132 R 2. Bereich obere Grenze None MC34 Recipe Lower limit Std dev -1 R None None MC35 Recipe Upper limit Std dev -1 R None None MC36 Recipe Section 3 None None None None MC37 Recipe Number of lines 1 R 3. Bereich Anzahl Linien None MC38 Recipe Lower limit 0.077 R 3. Bereich untere Grenze None MC39 Recipe Nominal value 0.1 R 3. Bereich Sollwert None MC40 Recipe Upper limit 0.132 R 3. Bereich obere Grenze None MC41 Recipe Lower limit Std dev -1 R None None MC42 Recipe Upper limit Std dev -1 R None None MC43 Recipe Path tracking (P2/P3 only) On R Bahnverfolgung Rezept eingeschaltet None MC44 Beam group 1 Powermap None None None None MC45 Beam group 1 initial attenuation(%) 4 A Attenuation low (%) 342bb397-526a-4949-bc31-d992bc8fbe80 MC46 Beam group 1 FiN/Al attenuation(%) 99 A Attenuation high (%) 1248b408-8ebe-4a92-8f1c-b2a6593a3297 MC47 Beam group 1 Attenuation increment(%) 5 A Attenuation step (%) 27486c1d-8c5b-47fe-91b1-abffbbcec9a4 MC48 Beam group 1 Initial frequency(kHz) 1000 R Frequenz low [kHz] 78c62ff7-0d8f-45b0-b061-bdc3b97271a2 MC49 Beam group 1 FiN/Al frequency(kHz) 1000 R Frequenz high [kHz] ec972836-f12b-4740-a3d7-162989cc43b2 MC50 Beam group 1 Frequency increment(kHz) 10 A Frequenz step [kHz] 94ffba7f-60b3-4d9a-bf4e-7bb8fdc63907 MC51 Beam group 1 Laser measurement None None None None MC52 Beam group 1 Power window % 23 A erlaubte Abweichung externe Leistung [%] d1b66ce6-6898-4c77-9682-8b1bf1516949 MC53 Beam group 1 Error setting target power: check R Anlagenstopp bei Fehler Setzen der Sollleistung 49ab3617-989c-436a-be41-7ee1ae60446a MC54 Beam group 1 Faulty power measurement: check R Anlagenstop bei Leistungsmessfehler c7aa2ada-d1de-4d84-b840-44cb47ea1841 MC55 Beam group 1 after _____ substrate power measurement 175 A Zyklus Leistungsmessung b00f6248-a0c1-4389-8b40-550eca311968 MC56 Beam group 2 Powermap None None None None MC57 Be